In [17]:
#import all your libraries from NBA_API
from nba_api.stats.endpoints import boxscoretraditionalv2, boxscoreplayertrackv2, boxscoresummaryv2, playerdashboardbygamesplits, playerdashboardbyshootingsplits, playerdashboardbygeneralsplits, shotchartdetail, scoreboardv2, teamplayeronoffsummary, teamplayeronoffdetails, leaguedashplayershotlocations, defensehub, playergamelog, teamdashlineups, leaguedashptteamdefend, leaguedashptdefend
from nba_api.stats.endpoints import playbyplay, playbyplayv2,leaguegamefinder, SynergyPlayTypes, playbyplayv2, playerawards, PlayByPlayV2, leaguegamelog, winprobabilitypbp, WinProbabilityPBP, PlayerDashPtShots, playerdashptshots
from nba_api.live.nba.endpoints import playbyplay
import pandas as pd


## ODDS API

In [74]:
import requests
import pandas as pd
from datetime import datetime, timedelta

start_date = datetime(2020, 7, 30)
end_date = datetime.now()
current_date = start_date
games_fetched = 0
max_games = 1  # Limit to the first 10 games
data = []
delta = timedelta(days=1) 
apiKey = 'd014e3c2549e083b808097e7aebf0ad6'

while current_date <= end_date:
    date_str = current_date.strftime('%Y-%m-%dT23:59:59Z')
    url = f'https://api.the-odds-api.com//v4/historical/sports/basketball_nba/odds?apiKey={apiKey}&regions=us&markets=spreads&date={date_str}'
    response = requests.get(url)
    odds_data = response.json()
    if 'data' in odds_data:
        for game in odds_data['data']:
            games_fetched+=1
            if 'bookmakers' in game and game['bookmakers']:
                # Process each site's odds and determine the favored team
                latest_spread_info = None
                for site in game['bookmakers']:
                    if site['last_update'] < game['commence_time']:

                        markets = site['markets']
                        for market in markets:
                            if market['key'] == 'spreads':
                                first_outcome = market['outcomes'][0]
                                point = first_outcome['point']
                                if point <= 0:
                                    favored_team = first_outcome['name']
                                    price = first_outcome['price']
                                    underdog_team = market['outcomes'][1]['name']
                                else:
                                    underdog_team = first_outcome['name']
                                    price = first_outcome['price']
                                    favored_team = market['outcomes'][1]['name']
                                game_datetime = datetime.fromisoformat(game['commence_time'].replace('Z', '+00:00'))
                                if game_datetime.hour < 12:  # Before noon UTC, adjust to previous day
                                    game_datetime -= timedelta(days=1)
                                adjusted_game_date_str = game_datetime.strftime('%Y-%m-%d')
                                datetime_obj = datetime.fromisoformat(date_str.replace('Z', '+00:00'))
                                date_str = datetime_obj.strftime('%Y-%m-%d')
                                # Check if the adjusted game date is the same as the API call date
                                if adjusted_game_date_str == date_str:
                                    latest_spread_info = {
                                        'date': adjusted_game_date_str,
                                        'favored_team': favored_team,
                                        'underdog_team': underdog_team,
                                        'spread': abs(point),
                                    }
                    
                if latest_spread_info:
                    data.append(latest_spread_info)
                    games_fetched+=1
    
    current_date += timedelta(days=1)

df = pd.DataFrame(data)
df.to_csv('Spreads_Historic', index=False)

In [18]:
#Get database of games
gamefinder = leaguegamefinder.LeagueGameFinder(league_id_nullable='00')
games = gamefinder.get_data_frames()[0]


In [19]:
spreads = pd.read_csv('Spreads_Historic.csv')

# Prepare spreads DataFrame by renaming and adjusting the structure for merging
spreads_favored = spreads.rename(columns={'date': 'GAME_DATE', 'favored_team': 'TEAM_NAME', 'spread': 'ADJUSTED_SPREAD'})
spreads_underdog = spreads.rename(columns={'date': 'GAME_DATE', 'underdog_team': 'TEAM_NAME'})

# Adjust the spread: multiply by -1 for favored teams
spreads_favored['ADJUSTED_SPREAD'] *= -1

# Merge the games DataFrame with the spreads DataFrame on the conditions provided
result_favored = pd.merge(games, spreads_favored, on=['TEAM_NAME', 'GAME_DATE'])
result_underdog = pd.merge(games, spreads_underdog, on=['TEAM_NAME', 'GAME_DATE'])

# Combine the results from both merge operations
result = pd.concat([result_favored, result_underdog]).drop_duplicates()

# Display the result
print(result)

     SEASON_ID     TEAM_ID TEAM_ABBREVIATION              TEAM_NAME  \
0        42023  1610612739               CLE    Cleveland Cavaliers   
1        42023  1610612752               NYK        New York Knicks   
2        42023  1610612754               IND         Indiana Pacers   
3        42023  1610612743               DEN         Denver Nuggets   
4        42023  1610612760               OKC  Oklahoma City Thunder   
...        ...         ...               ...                    ...   
4101     22019  1610612745               HOU        Houston Rockets   
4102     22019  1610612761               TOR        Toronto Raptors   
4103     22019  1610612745               HOU        Houston Rockets   
4104     22019  1610612759               SAS      San Antonio Spurs   
4105     22019  1610612746               LAC            LA Clippers   

         GAME_ID   GAME_DATE      MATCHUP WL  MIN  PTS  ...  AST  STL  BLK  \
0     0042300135  2024-04-30  CLE vs. ORL  W  241  104  ...   23    9

In [20]:
df = result
df['FINAL_SPREAD'] = df['ADJUSTED_SPREAD'].fillna(df['spread'])

# Optionally drop the original columns if they are no longer needed
df.drop(columns=['ADJUSTED_SPREAD', 'spread'], inplace=True)

In [21]:
games = df
games_info = games[['GAME_ID', 'TEAM_ID', 'WL', 'PLUS_MINUS', 'FINAL_SPREAD', 'GAME_DATE']]

In [7]:
import pandas as pd

# Assuming games_info is your dataframe
# Example: games_info = pd.read_csv('your_data.csv')

# Calculate the correlation between PLUS_MINUS and FINAL_SPREAD
correlation = games_info['PLUS_MINUS'].corr(games_info['FINAL_SPREAD'])
print(f"Correlation between PLUS_MINUS and FINAL_SPREAD: {correlation}")

# Calculate the average error between PLUS_MINUS and FINAL_SPREAD
average_error = (games_info['PLUS_MINUS'] - games_info['FINAL_SPREAD']).abs().mean()
print(f"Average error between PLUS_MINUS and FINAL_SPREAD: {average_error}")


Correlation between PLUS_MINUS and FINAL_SPREAD: -0.4514272561179378
Average error between PLUS_MINUS and FINAL_SPREAD: 15.399975645396982


In [22]:
unique_areas = set()
unique_area_details = set()
unique_action_types = set()
count = 0

sampled_df = games_info.sample(n=50)
for game in sampled_df.itertuples():
    game_id = game.GAME_ID
    # Get the teamId for the current game
    #team_id = games.loc[games['GAME_ID'] == game_id, 'TEAM_ID'].iloc[0]
    # Instantiate PlayByPlay for the current game
    pbp = playbyplay.PlayByPlay(game_id=game_id)
    
    # Fetch the plays data
    plays = pbp.get_dict()['game']['actions']
    plays_df = pd.DataFrame(plays)
    if 'area' in plays_df.columns:
        unique_areas.update(plays_df['area'].unique())
    if 'areaDetail' in plays_df.columns:
        unique_area_details.update(plays_df['areaDetail'].unique())
    if 'actionType' in plays_df.columns:
        unique_action_types.update(plays_df['actionType'].unique())
    
    

# Convert sets to lists (optional, useful for indexing/ordering if needed later)
unique_areas = list(unique_areas)
unique_area_details = list(unique_area_details)
unique_action_types = list(unique_action_types)
unique_areas = [area for area in unique_areas if pd.notna(area)]
unique_area_details = [area for area in unique_area_details if pd.notna(area)]
unique_action_types = [area for area in unique_action_types if pd.notna(area)]


In [54]:
plays_df

actionNumber        clock              timeActual  period periodType  \
0               2  PT12M00.00S  2023-11-16T00:41:00.7Z       1    REGULAR   
1               4  PT11M58.00S  2023-11-16T00:41:02.6Z       1    REGULAR   
2               7  PT11M45.00S  2023-11-16T00:41:15.2Z       1    REGULAR   
3               8  PT11M43.00S  2023-11-16T00:41:17.2Z       1    REGULAR   
4               9  PT11M43.00S  2023-11-16T00:41:23.1Z       1    REGULAR   
..            ...          ...                     ...     ...        ...   
577           698  PT00M15.80S  2023-11-16T02:54:51.2Z       4    REGULAR   
578           701  PT00M15.80S  2023-11-16T02:55:19.8Z       4    REGULAR   
579           702  PT00M15.80S  2023-11-16T02:55:30.8Z       4    REGULAR   
580           703  PT00M00.00S  2023-11-16T02:55:54.0Z       4    REGULAR   
581           704  PT00M00.00S  2023-11-16T02:55:57.1Z       4    REGULAR   

    actionType    subType               qualifiers  personId          x  \
0       period      start                       []         0        NaN   
1     jumpball  recovered                       []   1641748        NaN   
2          2pt  Jump Shot       [pointsinthepaint]    201572  83.130749   
3      rebound  defensive                       []   1627783        NaN   
4     turnover  traveling                       []   1627783        NaN   
..         ...        ...                      ...       ...        ...   
577       foul   personal  [inpenalty, 2freethrow]   1629623        NaN   
578  freethrow     1 of 2                       []   1641806        NaN   
579  freethrow     2 of 2                       []   1641806        NaN   
580     period        end                       []         0        NaN   
581       game        end                       []         0        NaN   

             y  possession scoreHome scoreAway                edited  \
0          NaN           0         0         0  2023-11-16T00:41:00Z   
1          NaN  1610612749         0         0  2023-11-16T00:41:02Z   
2    51.960784  1610612749         0         0  2023-11-16T02:34:02Z   
3          NaN  1610612761         0         0  2023-11-16T02:34:02Z   
4          NaN  1610612761         0         0  2023-11-16T00:41:37Z   
..         ...         ...       ...       ...                   ...   
577        NaN  1610612761       110       128  2023-11-16T02:55:03Z   
578        NaN  1610612761       111       128  2023-11-16T02:55:19Z   
579        NaN  1610612761       112       128  2023-11-16T02:55:30Z   
580        NaN  1610612749       112       128  2023-11-16T02:55:54Z   
581        NaN           0       112       128  2023-11-16T02:55:57Z   

     orderNumber  isTargetScoreLastPeriod  xLegacy  yLegacy  isFieldGoal  \
0          20000                    False      NaN      NaN            0   
1          40000                    False      NaN      NaN            0   
2          70000                    False     10.0    106.0            1   
3          80000                    False      NaN      NaN            0   
4          90000                    False      NaN      NaN            0   
..           ...                      ...      ...      ...          ...   
577      6870000                    False      NaN      NaN            0   
578      6890000                    False      NaN      NaN            0   
579      6900000                    False      NaN      NaN            0   
580      6910000                    False      NaN      NaN            0   
581      6920000                    False      NaN      NaN            0   

      side                                        description  \
0     None                                       Period Start   
1     None  Jump Ball B. Lopez vs. J. Poeltl: Tip to A. Ja...   
2    right                    MISS B. Lopez 10' fadeaway Shot   
3     None                    P. Siakam REBOUND (Off:0 Def:1)   
4     None                P. Siakam traveling TURNOVER (1 TO)   
..     ... 

In [9]:
pd.set_option('display.max_rows', 10)
number = 1610613
number_str = str(number)
result_str = '00' + number_str

#shots = leaguedashplayershotlocations.LeagueDashPlayerShotLocations(distance_range="By Zone",per_mode_detailed= "Per100Possessions", date_from_nullable= "2020-11-16", date_to_nullable= "2023-11-16")
shots = leaguedashplayershotlocations.LeagueDashPlayerShotLocations(season="2023-24", distance_range="By Zone",per_mode_detailed= "Per100Possessions", date_to_nullable= "2023-10-24")
json = shots.get_dict()
headers = json['resultSets']['headers'][1]['columnNames']
rows = json['resultSets']['rowSet']
df = pd.DataFrame(rows, columns=headers)
df

PLAYER_ID     PLAYER_NAME     TEAM_ID TEAM_ABBREVIATION   AGE NICKNAME  \
0      203932    Aaron Gordon  1610612743               DEN  28.0    Aaron   
1      203952  Andrew Wiggins  1610612744               GSW  29.0   Andrew   
2      203076   Anthony Davis  1610612747               LAL  31.0  Anthony   
3     1630559   Austin Reaves  1610612747               LAL  26.0   Austin   
4     1630296     Braxton Key  1610612743               DEN  27.0  Braxton   
..        ...             ...         ...               ...   ...      ...   
39    1629060   Rui Hachimura  1610612747               LAL  26.0      Rui   
40     201939   Stephen Curry  1610612744               GSW  36.0  Stephen   
41    1627752  Taurean Prince  1610612747               LAL  30.0  Taurean   
42    1629139   Yuta Watanabe  1610612763               MEM  29.0     Yuta   
43    1630192      Zeke Nnaji  1610612743               DEN  23.0     Zeke   

     FGM   FGA  FG_PCT   FGM  ...  FG_PCT   FGM   FGA  FG_PCT  FGM   FGA  \
0   26.1  30.4   0.857   0.0  ...     0.0   4.5   4.5   1.000  NaN   NaN   
1   10.0  20.0   0.500  21.4  ...     0.0   0.0  13.0   0.000  0.0   0.0   
2   13.0  21.7   0.600  10.5  ...     0.0   4.8   9.5   0.500  NaN   NaN   
3    8.0  12.0   0.667   0.0  ...     0.0   6.7  13.3   0.500  NaN   NaN   
4    NaN   NaN     NaN   0.0  ...     NaN   NaN   NaN     NaN  NaN   NaN   
..   ...   ...     ...   ...  ...     ...   ...   ...     ...  ...   ...   
39  27.3  63.6   0.429   0.0  ...     0.0   0.0  33.3   0.000  NaN   NaN   
40   0.0   0.0   0.000  18.2  ...     0.0  11.5  46.2   0.250  0.0  33.3   
41   4.0   4.0   1.000   5.9  ...     0.5  21.4  21.4   1.000  NaN   NaN   
42   0.0   0.0   0.000   6.3  ...     0.0  13.3  20.0   0.667  0.0   0.0   
43  33.3  66.7   0.500   0.0  ...     0.0   0.0  12.5   0.000  0.0   0.0   

    FG_PCT   FGM    FGA  FG_PCT  
0      NaN   0.0   20.0   0.000  
1      0.0   0.0    0.0   0.000  
2      NaN   0.0    0.0   0.000  
3      NaN   0.0    0.0   0.000  
4      NaN   NaN    NaN     NaN  
..     ...   ...    ...     ...  
39     NaN   0.0    0.0   0.000  
40     0.0  33.3   33.3   1.000  
41     NaN  25.0   75.0   0.333  
42     0.0   0.0  100.0   0.000  
43     0.0   0.0    0.0   0.000  

[44 rows x 30 columns]

In [33]:
import pandas as pd
from datetime import datetime, timedelta
import time
#Function that takes actions and turns them into usable for encoding
def fetch_season_data(season, date_from_nullable=None, date_to_nullable=None, suffix=""):
    shots = leaguedashplayershotlocations.LeagueDashPlayerShotLocations(
        season=season, distance_range="By Zone",
        date_from_nullable=date_from_nullable, date_to_nullable=date_to_nullable
    )
    json = shots.get_dict()
    headers = json['resultSets']['headers'][1]['columnNames']
    rows = json['resultSets']['rowSet']
    df= pd.DataFrame(rows, columns=headers)
    cols = df.columns
    unique_headers = []
    header_counts = {}
    for header in cols:
        if header in header_counts:
            header_counts[header] += 1
            unique_headers.append(f"{header}_{header_counts[header]}_{suffix}")
        else:
            header_counts[header] = 1
            unique_headers.append(f"{header}_{header_counts[header]}_{suffix}")
    df.columns = unique_headers
    return df



def transform_actions(actions, team_id, game_date):
    # Parse 'clock' to seconds remaining in the game
    actions['clock_seconds'] = actions['clock'].str.extract(r'PT(\d+)M(\d+.\d+)S').apply(
        lambda x: int(x[0]) * 60 + float(x[1]), axis=1)

    # Create boolean variables for each unique string in 'actionType'
    if 'actionType' not in actions.columns:
        actions['actionType'] = 0
    actions['actionType'] = pd.Categorical(actions['actionType'], categories=unique_action_types)

        
    action_types = pd.get_dummies(actions['actionType'])
    actions = pd.concat([actions, action_types], axis=1)

    # Define the list of subtypes to create booleans for
    subtypes_of_interest = ['Jump Shot', 'Layup', 'Hook', 'DUNK', 'bad pass', 'out', 'in', 'offensive foul']
    for subtype in subtypes_of_interest:
        actions[f'subtype_{subtype}'] = actions['subType'].apply(lambda x: x == subtype)

    # Create booleans for specified qualifiers
    qualifiers_of_interest = ['2ndchance', 'pointsinthepaint', 'fromturnover', 'fastbreak']
    for qualifier in qualifiers_of_interest:
        actions[f'qualifier_{qualifier}'] = actions['qualifiers'].apply(lambda x: qualifier in str(x))

    # Convert 'scorehome' and 'scoreaway' to numeric
    actions['scorehome'] = pd.to_numeric(actions['scoreHome'])
    actions['scoreaway'] = pd.to_numeric(actions['scoreAway'])

    # Create a boolean column to indicate if the teamId matches
    actions['is_team_action'] = actions['teamId'] == team_id

    # Create boolean variables for 'side's unique values
    side_booleans = pd.get_dummies(actions['side'], prefix='side')
    actions = pd.concat([actions, side_booleans], axis=1)

    # Create boolean variables for 'area's unique values
    if 'area' not in actions.columns:
        actions['area'] = 0
    actions['area'] = pd.Categorical(actions['area'], categories=unique_areas)

    area_booleans = pd.get_dummies(actions['area'], prefix='area')
    actions = pd.concat([actions, area_booleans], axis=1)

    # Create boolean variables for 'areaDetail's unique values
    if 'areaDetail' not in actions.columns:
        actions['areaDetail'] = 0
    actions['areaDetail'] = pd.Categorical(actions['areaDetail'], categories=unique_area_details)

    areaDetail_booleans = pd.get_dummies(actions['areaDetail'], prefix='areaDetail')
    actions = pd.concat([actions, areaDetail_booleans], axis=1)

    # Create boolean variables for 'shotResult's unique values
    shotResult_booleans = pd.get_dummies(actions['shotResult'], prefix='shotResult')
    actions = pd.concat([actions, shotResult_booleans], axis=1)

    # Keep specified numeric variables and the new 'is_team_action' boolean
    numeric_columns = ['period', 'x', 'y', 'xLegacy', 'yLegacy', 'isFieldGoal', 'personId', 'shotDistance',
                       'shotActionNumber', 'reboundTotal', 'reboundDefensiveTotal',
                       'reboundOffensiveTotal', 'pointsTotal', 'assistTotal', 'turnoverTotal',
                       'foulPersonalTotal','clock_seconds', 'is_team_action']

    # Determine columns to keep
    columns_to_keep = numeric_columns + list(action_types.columns) + \
                      [f'subtype_{subtype}' for subtype in subtypes_of_interest] + \
                      [f'qualifier_{qualifier}' for qualifier in qualifiers_of_interest]+ \
                      list(side_booleans.columns) + list(area_booleans.columns) + \
                      list(areaDetail_booleans.columns) + list(shotResult_booleans.columns)

    # Return the transformed DataFrame
    actions =  actions[columns_to_keep]
    
    # Parse the given date
    game_date_dt = datetime.strptime(game_date, "%Y-%m-%d")

    # Determine the current and previous seasons
    current_season = f"{game_date_dt.year}-{str(game_date_dt.year + 1)[-2:]}"
    previous_season = f"{game_date_dt.year - 1}-{str(game_date_dt.year)[-2:]}"
    previous_season_2 = f"{game_date_dt.year - 2}-{str(game_date_dt.year-1)[-2:]}"
    df_current = fetch_season_data(current_season, date_to_nullable=game_date, suffix="curr")
    time.sleep(0.5)
    try:
        previous_date = game_date_dt.replace(year=game_date_dt.year - 1).strftime("%Y-%m-%d")
    except ValueError:
        previous_date = game_date_dt.replace(year=game_date_dt.year - 1, day=28).strftime("%Y-%m-%d")
            
    df_previous = fetch_season_data(previous_season, date_from_nullable=previous_date, suffix="prev") 
    time.sleep(0.5)
    df_previous_2 = fetch_season_data(previous_season_2, date_from_nullable=previous_date, suffix="prev_2") 
    
    df_merged = pd.merge(df_current, df_previous, left_on='PLAYER_ID_1_curr', right_on='PLAYER_ID_1_prev', how='outer', suffixes=('', '_drop'))
    df_merged['PLAYER_ID'] = df_merged['PLAYER_ID_1_curr'].combine_first(df_merged['PLAYER_ID_1_prev'])

    # Drop the old PLAYER_ID columns if needed
    df_merged = df_merged.drop(columns=['PLAYER_ID_1_curr', 'PLAYER_ID_1_prev'])
    
    
    df_merged = pd.merge(df_merged, df_previous_2, left_on='PLAYER_ID', right_on='PLAYER_ID_1_prev_2', how='outer', suffixes=('', '_drop'))
    # Summing FGA and FGM columns and recalculating FG_PCT
    for i in range(1, 9):
        fgm_col_curr = f"FGM_{i}_curr"
        fga_col_curr = f"FGA_{i}_curr"
        fgm_col_prev = f"FGM_{i}_prev"
        fga_col_prev = f"FGA_{i}_prev"
        fga_col_prev_2 = f"FGA_{i}_prev_2"
        fgm_col_prev_2 = f"FGM_{i}_prev_2"
        
        # Handle cases where columns might not exist in both DataFrames
        if fgm_col_curr in df_merged.columns and fgm_col_prev in df_merged.columns:
            df_merged[f"FGM_{i}"] = df_merged[fgm_col_curr].fillna(0) + df_merged[fgm_col_prev].fillna(0) + df_merged[fgm_col_prev_2].fillna(0)
        elif fgm_col_curr in df_merged.columns:
            df_merged[f"FGM_{i}"] = df_merged[fgm_col_curr].fillna(0)
        elif fgm_col_prev in df_merged.columns:
            df_merged[f"FGM_{i}"] = df_merged[fgm_col_prev].fillna(0)

        if fga_col_curr in df_merged.columns and fga_col_prev in df_merged.columns:
            df_merged[f"FGA_{i}"] = df_merged[fga_col_curr].fillna(0) + df_merged[fga_col_prev].fillna(0) + df_merged[fga_col_prev_2].fillna(0)
        elif fga_col_curr in df_merged.columns:
            df_merged[f"FGA_{i}"] = df_merged[fga_col_curr].fillna(0)
        elif fga_col_prev in df_merged.columns:
            df_merged[f"FGA_{i}"] = df_merged[fga_col_prev].fillna(0)
            
        # Calculate FG_PCT
        df_merged[f"FG_PCT_{i}"] = df_merged[f"FGM_{i}"] / df_merged[f"FGA_{i}"]
        df_merged[f"FG_PCT_{i}"] = df_merged[f"FG_PCT_{i}"].replace([float('inf'), -float('inf')], 0).fillna(0)

    # Drop the unnecessary columns and intermediate columns
    columns_to_drop = [col for col in df_merged.columns if 'curr' in col or 'prev' in col or any(key in col for key in ['PLAYER_NAME', 'TEAM_ID', 'TEAM_ABBREVIATION', 'AGE', 'NICKNAME'])]
    df_merged = df_merged.drop(columns=columns_to_drop)
    
    result = actions.merge(df_merged, left_on='personId', right_on='PLAYER_ID', how='left')
    
        # Ensure unique column names
    unique_headers = []
    header_counts = {}
    for header in result.columns:
        if header in header_counts:
            header_counts[header] += 1
            unique_headers.append(f"{header}_{header_counts[header]}")
        else:
            header_counts[header] = 0
            unique_headers.append(header)

    result.columns = unique_headers

    
    joined_columns = [col for col in df_merged.columns if col != 'PLAYER_ID']
    result.loc[result['personId'] == 0, joined_columns] = 0
    rslt_df = result.loc[result['isFieldGoal'] == 1]
    rslt_df = rslt_df.loc[rslt_df['period'] <= 2] 
    rslt_df = rslt_df.drop(columns=["period", "period_1", "period_2", "period_3", 'personId', 'PLAYER_ID'])

    return rslt_df

# Example usage:
# team_id = games.loc[games['GAME_ID'] == game_id, 'teamId'].iloc[0]
# actions_final = transform_actions(final_plays_df, team_id)


In [24]:
pd.set_option('display.max_rows', 20)
pd.set_option('display.max_columns', 100)
import json
def get_plays_dataframe(game):
    game_id = game[0]
    team_id = game[1]
    # Get the teamId for the current game
    #team_id = games.loc[games['GAME_ID'] == game_id, 'TEAM_ID'].iloc[0]
    # Instantiate PlayByPlay for the current game
    pbp = playbyplay.PlayByPlay(game_id=game_id)
    # Fetch the plays data
    plays = pbp.get_dict()['game']['actions']
    
    # Create a DataFrame from the plays data
    plays_df = pd.DataFrame(plays)
    "we are about to transform_actions"
    # Transform the plays DataFrame using the team_id
    actions_final = transform_actions(plays_df, team_id, game[5])
    actions_final['spread'] = game[4]
    
    return actions_final
    


In [36]:
import numpy as np
import os
from datetime import datetime, timedelta
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Bidirectional, LSTM, Dropout, Dense
from tensorflow.keras.optimizers import Adam
# Model configuration
n_features = 94  # Number of features per play
n_units = 256  # Number of hidden units
dropout_rate = 0
# Model configuration
model = Sequential([
    # First LSTM layer
    Bidirectional(LSTM(128, return_sequences=True), input_shape=(None, n_features)),
    Dropout(dropout_rate),
    Bidirectional(LSTM(64, return_sequences=True)),
    Dropout(dropout_rate),
    # Additional dense layers to capture more non-linearities and interactions
    Dense(64, activation='relu'),
    Dropout(dropout_rate),
    Dense(50, activation='relu'),
    Dropout(dropout_rate),
    # Output layer
    Dense(1)  # Predicting a single continuous value
])

model.compile(optimizer=Adam(), loss='mean_squared_error')

print("Model has been compiled.")

batch_folder = 'batch_data'  # Folder to store batch data

# Create directory if it does not exist
if not os.path.exists(batch_folder):
    os.makedirs(batch_folder)

# Training configuration
n_games_per_batch = 16  # Number of games to process per batch
n_epochs = 250  # Number of epochs to train

# Assuming 'games_info' is your DataFrame containing game IDs
train_indices = np.random.rand(len(games_info)) < 0.75
train_games_info = games_info[train_indices]
test_games_info = games_info[~train_indices]

loss_history = []

for epoch in range(n_epochs):
    # Randomly sample game IDs for this batch
    batch_game_ids = np.random.choice(train_games_info.index, size=n_games_per_batch, replace=False)
    batch_input = []
    batch_labels = []
    combined_plays_df = pd.DataFrame(columns=list(train_games_info.columns) + ['Plays'])
    
    for idx in batch_game_ids:
        # Get plays for the current game
        game_info = tuple(train_games_info.iloc[idx])
        plays_df = get_plays_dataframe(game_info)
        if isinstance(plays_df, pd.DataFrame):
            plays_df.fillna(0, inplace=True)
            plays_df['game_id'] = game_info[0]
            plays_df['team_id'] = game_info[1]
            plays_list = plays_df.values.tolist()
            #combined_info = game_info.tolist() + [plays_list]
            #combined_plays_df = combined_plays_df.append(pd.Series(combined_info, index=combined_plays_df.columns), ignore_index=True)
            #if plays_df.shape[1] == 50:
            # Convert DataFrame to appropriate numpy array for training
            # Assuming 'features' are in the first 69 columns and 'PLUS_MINUS' is the label
            #print('plays_df_shape: ', plays_df.shape)
            features = plays_df.iloc[:, :94].values
            #print("x input", features)
            batch_input.append(features)
            batch_labels.append(game_info[3]) 
        else:
            print("noinstance", plays_df)
        print("game loaded")
# Pad sequences for consistent input size
    #timestamp = datetime.datetime.now().strftime("%Y%m%d%H%M%S")
    #csv_filename = f"{batch_folder}/batch_epoch_{epoch+1}_games_{len(batch_game_ids)}_{timestamp}.csv"
    
    # Save combined_plays_df to CSV
    #combined_plays_df.to_csv(csv_filename, index=False)
    #print(f"Saved batch data to {csv_filename}")
    
    if batch_input:
        batch_input_padded = tf.keras.preprocessing.sequence.pad_sequences(batch_input, padding='post', dtype='float32')
        batch_labels = np.array(batch_labels)
        
        
        timestamp = datetime.now().strftime("%Y%m%d%H%M%S")
        np.save(os.path.join(batch_folder, f'batch_input_{timestamp}.npy'), batch_input_padded)
        np.save(os.path.join(batch_folder, f'batch_labels_{timestamp}.npy'), batch_labels)

        # Train the model on this batch
        loss = model.train_on_batch(batch_input_padded, batch_labels)
        loss_history.append(loss)
        print(f"Epoch {epoch+1}/{n_epochs} completed.")
        print('Current loss: ', loss)
    else:
        print('No data for training in this batch')
        print(batch_input)

    # Validation step (optional, if you have validation data)
    if len(test_games_info) > 0 and (epoch+1) % 30 == 0:
        val_batch_game_ids = np.random.choice(test_games_info.index, size=16, replace=False)
        val_batch_input = []
        val_batch_labels = []

        for idx1 in val_batch_game_ids:
            game_info = tuple(test_games_info.iloc[idx])
            plays_df = get_plays_dataframe(game_info)
            if isinstance(plays_df, pd.DataFrame):
                plays_df.fillna(0, inplace=True)
                features = plays_df.iloc[:, :96].values
                val_batch_input.append(features)
                val_batch_labels.append(game_info['PLUS_MINUS'])  # Assuming 'PLUS_MINUS' is the label in game_info

        if val_batch_input:
            val_batch_input_padded = tf.keras.preprocessing.sequence.pad_sequences(val_batch_input, padding='post', dtype='float32')
            val_batch_labels = np.array(val_batch_labels)

            # Evaluate the model on the validation batch
            val_loss = model.evaluate(val_batch_input_padded, val_batch_labels, verbose=0)
            print(f"Validation loss: {val_loss}")
        else:
            print('No validation data for this batch')

print("Training complete.")


Model has been compiled.
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
Epoch 1/250 completed.
Current loss:  263.32171630859375
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
game loaded
Epoch 2/250 completed.
Current loss:  243.62965393066406
game loaded
game loaded
game loaded


ConnectionError: HTTPSConnectionPool(host='stats.nba.com', port=443): Read timed out.

In [37]:
import numpy as np
import os
from datetime import datetime, timedelta
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Bidirectional, LSTM, Dropout, Dense
from tensorflow.keras.optimizers import Adam
from tensorflow.keras import backend as K
import psutil

# Monitor memory usage
print(f"Memory usage: {psutil.virtual_memory().percent}%")
K.clear_session()
# Model configuration
n_features = 94  # Number of features per play
n_units = 256  # Number of hidden units
dropout_rate = 0.075
# Model configuration
model = Sequential([
    Bidirectional(LSTM(128, return_sequences=True), input_shape=(None, n_features)),
    Dropout(dropout_rate),
    Bidirectional(LSTM(64, return_sequences=True)),
    Dropout(dropout_rate),
    Dense(64, activation='relu'),
    Dense(32, activation='relu'),
    Dropout(dropout_rate),
    Dense(1)
])

optimizer = Adam(clipnorm=1.0)  # Clip gradients by norm, or you can use clipvalue

model.compile(optimizer=optimizer, loss='mean_squared_error')

# Directory containing the .npy files
data_dir = '/Users/ethangoldberg/NBAPoisson/batch_data'

# Initialize lists to store all inputs and labels
all_inputs = []
all_labels = []

# List all files in the directory
all_files = os.listdir(data_dir)

# Extract unique IDs from the filenames
unique_ids = set()
for filename in all_files:
    if filename.startswith('batch_input_') and filename.endswith('.npy'):
        unique_id = filename[len('batch_input_'):-len('.npy')]
        unique_ids.add(unique_id)

# Iterate through each unique ID and load corresponding input and label files
for unique_id in unique_ids:
    input_filepath = os.path.join(data_dir, f'batch_input_{unique_id}.npy')
    label_filepath = os.path.join(data_dir, f'batch_labels_{unique_id}.npy')

    if os.path.exists(input_filepath) and os.path.exists(label_filepath):
        batch_input = np.load(input_filepath)
        batch_label = np.load(label_filepath)
        if batch_input.shape[0]==16:
            all_inputs.append(batch_input)
            all_labels.append(batch_label)

# Find the maximum length of the sequences

# Pad all input arrays to the maximum length
reconfigured_inputs = []
reconfigured_labels = []


Memory usage: 62.4%


In [39]:

# Loop through each (16, 694, 94) array in the original list
label_arr = []
input_arr = []
for idx in range(len(all_inputs)):
    array = all_inputs[idx]
    labels = all_labels[idx]
    for idx2 in range(len(array)):
        instance = array[idx2]
        label = labels[idx2]
        df = pd.DataFrame(instance)
        filtered_df = df[df.iloc[:, 4] == 1]
        print(filtered_df.shape)
        label_arr.append(label)
        input_arr.append(filtered_df.iloc[:, :94].values)
labels_end = np.array(label_arr)

inputs_end = tf.keras.preprocessing.sequence.pad_sequences(input_arr, padding='pre', dtype='float32')
loss = model.train_on_batch(inputs_end, labels_end)
print(f"Training loss: {loss}")
# Monitor memory usage
print(f"Memory usage: {psutil.virtual_memory().percent}%")


(192, 94)
(176, 94)
(177, 94)
(172, 94)
(180, 94)
(165, 94)
(162, 94)
(180, 94)
(177, 94)
(164, 94)
(172, 94)
(166, 94)
(166, 94)
(175, 94)
(171, 94)
(166, 94)
(170, 94)
(190, 94)
(178, 94)
(157, 94)
(175, 94)
(178, 94)
(167, 94)
(175, 94)
(183, 94)
(194, 94)
(171, 94)
(172, 94)
(188, 94)
(179, 94)
(177, 94)
(164, 94)
(172, 94)
(184, 94)
(178, 94)
(175, 94)
(182, 94)
(160, 94)
(188, 94)
(179, 94)
(170, 94)
(172, 94)
(162, 94)
(166, 94)
(165, 94)
(164, 94)
(164, 94)
(186, 94)
(171, 94)
(182, 94)
(181, 94)
(189, 94)
(179, 94)
(177, 94)
(166, 94)
(169, 94)
(183, 94)
(184, 94)
(183, 94)
(180, 94)
(209, 94)
(167, 94)
(183, 94)
(189, 94)
(155, 94)
(162, 94)
(174, 94)
(197, 94)
(174, 94)
(180, 94)
(171, 94)
(180, 94)
(165, 94)
(185, 94)
(166, 94)
(185, 94)
(180, 94)
(186, 94)
(168, 94)
(183, 94)
(174, 94)
(195, 94)
(184, 94)
(190, 94)
(185, 94)
(178, 94)
(177, 94)
(184, 94)
(174, 94)
(154, 94)
(167, 94)
(176, 94)
(173, 94)
(164, 94)
(180, 94)
(173, 94)
(150, 94)
(190, 94)
(182, 94)
(185, 94)


In [1]:
all_inputs_padded.shape

NameError: name 'all_inputs_padded' is not defined

In [78]:
from datetime import datetime, timedelta

# Given date in the format YYYY-MM-DD
input_date = '2023-02-01'

# Parse the given date
date_parsed = datetime.strptime(input_date, '%Y-%m-%d')

In [11]:
# Plotting the training loss
import matplotlib.pyplot as plt
plt.figure(figsize=(10, 5))
plt.plot(range(1, 48 + 1), loss_history, marker='o')
plt.title('Training Loss per Epoch')
plt.xlabel('Epoch')
plt.ylabel('Loss')
plt.grid(True)
plt.show()

print("Training complete.")

NameError: name 'loss_history' is not defined

<Figure size 1000x500 with 0 Axes>

In [57]:

# Testing the model
test_input = []
test_labels = []
train_indices = np.random.rand(len(games_info)) < 0.75
train_games_info = games_info[train_indices]
test_games_info = games_info[~train_indices]

for idx in test_games_info.index[:50]:
    game_info = tuple(test_games_info.iloc[idx])
    plays_df = get_plays_dataframe(game_info)
    plays_df.fillna(0, inplace=True)
    features = plays_df.iloc[:, :73].values
    plus_minus = game_info[3]

    test_input.append(features)
    test_labels.append(plus_minus)

test_input_padded = tf.keras.preprocessing.sequence.pad_sequences(test_input, padding='post', dtype='float32')
test_labels = np.array(test_labels)

# Evaluate the model on the test set
predictions = model.predict(test_input_padded)
mse = tf.keras.losses.MeanSquaredError()
test_mse = mse(test_labels, predictions).numpy()

print("Test MSE:", test_mse)

transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
transformed
2/2 [==============================] - 3s 935ms/step
Test MSE: 284.07477


## Transformer Attempt

In [12]:
import numpy as np
import os
import datetime
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Bidirectional, LSTM, Dropout, Dense
from tensorflow.keras.optimizers import Adam


def get_positional_encoding(seq_len, d_model):
    angle_rates = 1 / np.power(10000, (2 * (np.arange(d_model)[np.newaxis, :] // 2)) / np.float32(d_model))
    angle_rads = np.arange(seq_len)[:, np.newaxis] * angle_rates
    angle_rads[:, 0::2] = np.sin(angle_rads[:, 0::2])
    angle_rads[:, 1::2] = np.cos(angle_rads[:, 1::2])
    return tf.cast(angle_rads, dtype=tf.float32)


class TransformerBlock(tf.keras.layers.Layer):
    def __init__(self, d_model, num_heads, dff, rate=0.1):
        super(TransformerBlock, self).__init__()
        self.att = tf.keras.layers.MultiHeadAttention(num_heads=num_heads, key_dim=d_model)
        self.ffn = tf.keras.Sequential([
          tf.keras.layers.Dense(dff, activation='relu'),
          tf.keras.layers.Dense(d_model)
        ])
        self.layernorm1 = tf.keras.layers.LayerNormalization(epsilon=1e-6)
        self.layernorm2 = tf.keras.layers.LayerNormalization(epsilon=1e-6)
        self.dropout1 = tf.keras.layers.Dropout(rate)
        self.dropout2 = tf.keras.layers.Dropout(rate)

    def call(self, inputs, training):
        attn_output = self.att(inputs, inputs)
        attn_output = self.dropout1(attn_output, training=training)
        out1 = self.layernorm1(inputs + attn_output)
        ffn_output = self.ffn(out1)
        ffn_output = self.dropout2(ffn_output, training=training)
        return self.layernorm2(out1 + ffn_output)


class CustomTransformer(tf.keras.Model):
    def __init__(self, num_layers, d_model, num_heads, dff, input_dim, rate=0.1, maximum_position_encoding=1000):
        super(CustomTransformer, self).__init__()
        self.d_model = d_model
        self.num_layers = num_layers

        self.embedding = tf.keras.layers.Dense(d_model, activation='linear')
        self.pos_encoding = self.get_positional_encoding(maximum_position_encoding, d_model)

        self.transformer_blocks = [TransformerBlock(d_model, num_heads, dff, rate) for _ in range(num_layers)]
        self.final_layer = tf.keras.layers.Dense(1)  # Output layer for predicting a single value
        self.dropout = tf.keras.layers.Dropout(rate)

    def get_positional_encoding(self, position, d_model):
        angle_rads = self.get_angles(np.arange(position)[:, np.newaxis],
                                     np.arange(d_model)[np.newaxis, :], d_model)
        angle_rads[:, 0::2] = np.sin(angle_rads[:, 0::2])  # apply sin to even indices in the array
        angle_rads[:, 1::2] = np.cos(angle_rads[:, 1::2])  # apply cos to odd indices
        pos_encoding = angle_rads[np.newaxis, ...]
        return tf.cast(pos_encoding, dtype=tf.float32)

    def get_angles(self, pos, i, d_model):
        angle_rates = 1 / np.power(10000, (2 * (i // 2)) / np.float32(d_model))
        return pos * angle_rates

    def call(self, x, training):
        seq_len = tf.shape(x)[1]
        x = self.embedding(x)  # Apply embedding
        x += self.pos_encoding[:, :seq_len, :]  # Add positional encoding
        x = self.dropout(x, training=training)

        for transformer in self.transformer_blocks:
            x = transformer(x, training)

        x = self.final_layer(x)  # Pass through the final layer
        return x





In [14]:
import pandas as pd
import numpy as np
import os
import tensorflow as tf

# Assuming 'games_info' is already loaded with 'game_id', 'team_id', and 'PLUS_MINUS'
games_info['id_pair'] = games_info['GAME_ID'].astype(str) + '_' + games_info['TEAM_ID'].astype(str)

# Model and training configuration
n_epochs = 250
n_features = 73  # Number of features per play
batch_folder = 'batch_data'
all_csv_files = [os.path.join(batch_folder, f) for f in os.listdir(batch_folder) if f.endswith('.csv')]

model = CustomTransformer(
    num_layers=4, d_model=128, num_heads=8, dff=512, input_dim=n_features, rate=0.1
)
model.compile(optimizer='adam', loss='mean_squared_error', metrics=['mean_squared_error'])

print("Model has been compiled.")

loss_history = []

for epoch in range(n_epochs):
    # Select a random CSV file
    random_csv = np.random.choice(all_csv_files)
    plays_df = pd.read_csv(random_csv, dtype={'game_id': str, 'team_id': str})

    # Get unique game_id, team_id pairings
    unique_pairs = plays_df[['game_id', 'team_id']].drop_duplicates()

    # Prepare batches
    batch_input = []
    batch_labels = []

    for index, row in unique_pairs.iterrows():
        # Filter plays_df to just that game_id, team_id pairing
        filtered_df = plays_df[(plays_df['game_id'] == row['game_id']) & (plays_df['team_id'] == row['team_id'])]
        print(filtered_df)
        # Assuming 'features' are in the first 73 columns
        features = filtered_df.iloc[:, :73].values
        batch_input.append(features)

        # Merge to get the PLUS_MINUS for that game, team pairing
        current_id_pair = f"{row['game_id']}_{row['team_id']}"
        plus_minus_value = games_info[games_info['id_pair'] == current_id_pair]['PLUS_MINUS'].values[0]
        print(current_id_pair, plus_minus_value)
        batch_labels.append(plus_minus_value)
    
    # Convert to TensorFlow dataset
    if batch_input and batch_labels:
        batch_input_padded = tf.keras.preprocessing.sequence.pad_sequences(batch_input, padding='post', dtype='float32')
        batch_labels = np.array(batch_labels)
        dataset = tf.data.Dataset.from_tensor_slices((batch_input_padded, batch_labels)).batch(32)  # Assuming a batch size of 32
        
        # Train the model on this batch
        history = model.fit(dataset, epochs=1)
        loss_history.extend(history.history['loss'])
        print(f"Epoch {epoch+1}/{n_epochs} completed. Current loss: {history.history['loss'][-1]}")
    else:
        print("No valid data available for this epoch.")

print("Training complete.")

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


Model has been compiled.
     period          x          y  xLegacy  yLegacy  isFieldGoal  \
0         1   0.000000   0.000000      0.0      0.0            0   
1         1   0.000000   0.000000      0.0      0.0            0   
2         1   0.000000   0.000000      0.0      0.0            0   
3         1   0.000000   0.000000      0.0      0.0            0   
4         1   5.206965   2.450980    238.0     -4.0            1   
..      ...        ...        ...      ...      ...          ...   
246       2   0.000000   0.000000      0.0      0.0            0   
247       2  96.209757  90.219056    201.0    -17.0            1   
248       2   0.000000   0.000000      0.0      0.0            0   
249       2   0.000000   0.000000      0.0      0.0            0   
250       2   0.000000   0.000000      0.0      0.0            0   

     shotDistance  shotActionNumber  reboundTotal  reboundDefensiveTotal  \
0            0.00               0.0           0.0                    0.0   
1     

KeyboardInterrupt: 

In [21]:
pbp = playbyplay.PlayByPlay(game_id="0022100684")
pd.set_option('display.max_rows', 100)
# Fetch the plays data
plays = pbp.get_dict()['game']['actions']

# Create a DataFrame from the plays data
plays_df = pd.DataFrame(plays)
plays_df.head(100)

actionNumber        clock              timeActual  period periodType  \
0              2  PT12M00.00S  2022-01-22T00:10:54.8Z       1    REGULAR   
1              4  PT11M57.00S  2022-01-22T00:10:56.9Z       1    REGULAR   
2              7  PT11M41.00S  2022-01-22T00:11:13.3Z       1    REGULAR   
3              8  PT11M37.00S  2022-01-22T00:11:17.3Z       1    REGULAR   
4              9  PT11M29.00S  2022-01-22T00:11:24.7Z       1    REGULAR   
5             11  PT11M16.00S  2022-01-22T00:11:37.0Z       1    REGULAR   
6             12  PT11M14.00S  2022-01-22T00:11:39.0Z       1    REGULAR   
7             13  PT10M58.00S  2022-01-22T00:11:56.3Z       1    REGULAR   
8             14  PT10M58.00S  2022-01-22T00:11:56.3Z       1    REGULAR   
9             15  PT10M54.00S  2022-01-22T00:12:00.3Z       1    REGULAR   
10            16  PT10M49.00S  2022-01-22T00:12:04.9Z       1    REGULAR   
11            18  PT10M23.00S  2022-01-22T00:12:32.8Z       1    REGULAR   
12            19  PT10M07.00S  2022-01-22T00:12:59.9Z       1    REGULAR   
13            21  PT09M53.00S  2022-01-22T00:13:13.9Z       1    REGULAR   
14            22  PT09M51.00S  2022-01-22T00:13:15.9Z       1    REGULAR   
15            23  PT09M51.00S  2022-01-22T00:13:19.2Z       1    REGULAR   
16            25  PT09M36.00S  2022-01-22T00:13:50.9Z       1    REGULAR   
17            27  PT09M23.00S  2022-01-22T00:14:02.9Z       1    REGULAR   
18            28  PT09M20.00S  2022-01-22T00:14:05.9Z       1    REGULAR   
19            29  PT09M12.00S  2022-01-22T00:14:15.1Z       1    REGULAR   
20            31  PT09M12.00S  2022-01-22T00:14:19.3Z       1    REGULAR   
21            32  PT08M59.00S  2022-01-22T00:17:19.7Z       1    REGULAR   
22            33  PT08M57.00S  2022-01-22T00:17:21.7Z       1    REGULAR   
23            34  PT08M48.00S  2022-01-22T00:17:30.9Z       1    REGULAR   
24            35  PT08M48.00S  2022-01-22T00:17:30.9Z       1    REGULAR   
25            36  PT08M44.00S  2022-01-22T00:17:35.2Z       1    REGULAR   
26            38  PT08M29.00S  2022-01-22T00:17:52.3Z       1    REGULAR   
27            40  PT08M17.00S  2022-01-22T00:18:17.2Z       1    REGULAR   
28            42  PT07M56.00S  2022-01-22T00:18:39.3Z       1    REGULAR   
29            44  PT07M37.00S  2022-01-22T00:18:57.2Z       1    REGULAR   
30            46  PT07M21.00S  2022-01-22T00:19:13.2Z       1    REGULAR   
31            48  PT07M12.00S  2022-01-22T00:19:22.9Z       1    REGULAR   
32            49  PT07M10.00S  2022-01-22T00:19:24.9Z       1    REGULAR   
33            50  PT06M59.00S  2022-01-22T00:19:38.2Z       1    REGULAR   
34            52  PT06M59.00S  2022-01-22T00:20:01.8Z       1    REGULAR   
35            53  PT06M59.00S  2022-01-22T00:20:01.8Z       1    REGULAR   
36            54  PT06M57.00S  2022-01-22T00:20:03.8Z       1    REGULAR   
37            55  PT06M48.00S  2022-01-22T00:20:28.8Z       1    REGULAR   
38            56  PT06M37.00S  2022-01-22T00:20:47.1Z       1    REGULAR   
39            57  PT06M30.00S  2022-01-22T00:20:54.1Z       1    REGULAR   
40            58  PT06M30.00S  2022-01-22T00:20:53.0Z       1    REGULAR   
41            59  PT06M30.00S  2022-01-22T00:20:53.6Z       1    REGULAR   
42            60  PT06M25.00S  2022-01-22T00:20:59.5Z       1    REGULAR   
43            61  PT06M22.00S  2022-01-22T00:21:02.5Z       1    REGULAR   
44            62  PT06M19.00S  2022-01-22T00:21:05.1Z       1    REGULAR   
45            63  PT06M17.00S  2022-01-22T00:21:10.6Z       1    REGULAR   
46            64  PT06M17.00S  2022-01-22T00:22:46.8Z       1    REGULAR   
47            65  PT06M17.00S  2022-01-22T00:22:46.8Z       1    REGULAR   
48            66  PT05M56.00S  2022-01-22T00:24:23.1Z       1    REGULAR   
49            67  PT05M53.00S  2022-01-22T00:24:26.1Z       1    REGULAR   
50            68  PT05M46.00S  2022-01-22T00:24:32.8Z       1    REGULAR   
51            69  PT05M44.00S  2022-01-22T00:24:34.8